<h1 style='text-align:center'>Learning Cloth Dynamics: 3D+Texture Garment Reconstruction Challenge</h1>
<h2 style='text-align:center'>Starter Kit: Demo</h2>

In [1]:
# Preparing the environment
%load_ext autoreload
%autoreload 2
%matplotlib notebook
%matplotlib inline

import sys
sys.path.append('../DataReader')
from read import DataReader
from prepare_data import prepare_amass as prepare_cloth3D
import trimesh

""" Utils for this notebook """
import os
import os.path as osp
import shutil
from random import choice
import numpy as np
import plotly.graph_objs as go

from human_body_prior.tools.omni_tools import makepath, log2file
from human_body_prior.tools.omni_tools import copy2cpu as c2c
from util import loadInfo
from pprint import PrettyPrinter

In [2]:
expr_code = 'dataset' #VERSION_SUBVERSION_TRY
amass_dir = '/home/ICT2000/yxiu/Data/CLOTH3D/'
work_dir = os.path.join(amass_dir, expr_code)

amass_track_1_dir = os.path.join(amass_dir, 'CLOTH3D', 'train')

amass_train_dir = amass_track_1_dir.replace("train", "cloth3d_train")
amass_vald_dir = amass_track_1_dir.replace("train", "cloth3d_valid")
amass_test_dir = amass_track_1_dir.replace("train", "cloth3d_test")

if not (osp.exists(amass_test_dir) 
        and osp.exists(amass_vald_dir) and osp.exists(amass_train_dir)):

    all_ids = os.listdir(amass_track_1_dir)
    train_ratio = 0.9
    vald_ratio = 0.2

    train_ids = np.random.choice(all_ids, int(len(all_ids) * train_ratio), replace=False)
    val_test_ids = list(set(all_ids).difference(set(train_ids)))
    vald_ids = np.random.choice(val_test_ids, int(len(val_test_ids) * vald_ratio), replace=False)
    test_ids = list(set(val_test_ids).difference(set(vald_ids)))

    print(f"train:{len(train_ids)} vald:{len(vald_ids)}, test:{len(test_ids)} \n")

    os.makedirs(amass_train_dir, exist_ok=True)
    os.makedirs(amass_vald_dir, exist_ok=True)
    os.makedirs(amass_test_dir, exist_ok=True)

    for train_id in train_ids:
        os.symlink(src=os.path.join(amass_track_1_dir, train_id),
                        dst=os.path.join(amass_train_dir, train_id))
    
    for test_id in test_ids:
        os.symlink(src=os.path.join(amass_track_1_dir, test_id),
                        dst=os.path.join(amass_test_dir, test_id))

    for vald_id in vald_ids:
        os.symlink(src=os.path.join(amass_track_1_dir, vald_id),
                        dst=os.path.join(amass_vald_dir, vald_id))

In [121]:
msg = ''' Initial use of standard AMASS dataset preparation pipeline '''

logger = log2file(os.path.join(work_dir, '%s.log' % (expr_code)))
logger('[%s] AMASS Data Preparation Began.'%expr_code)
logger(msg)

amass_splits = {
    'vald': ['cloth3d_valid'],
    'test': ['cloth3d_test'],
    'train': ['cloth3d_train']
}


[dataset] AMASS Data Preparation Began.
 Initial use of standard AMASS dataset preparation pipeline 


In [122]:
prepare_cloth3D(amass_splits, os.path.join(amass_dir, 'CLOTH3D'), work_dir, logger=logger)

Stage I: Fetch data from AMASS npz files
randomly selecting data points from cloth3d_valid.
100%|██████████| 129/129 [00:00<00:00, 933.27it/s]
randomly selecting data points from cloth3d_test.
100%|██████████| 519/519 [00:00<00:00, 976.68it/s]
randomly selecting data points from cloth3d_train.
100%|██████████| 5827/5827 [00:04<00:00, 1170.93it/s]
Stage II: augment the data and save into h5 files to be used in a cross framework scenario.
vald has 31334 data points!
123it [00:03, 32.69it/s]
test has 128202 data points!
501it [00:12, 40.26it/s]
train has 1424826 data points!
5566it [02:09, 42.99it/s]

Stage III: dump every data field for all the splits as final pytorch pt files
Dumped final pytorch dataset at /home/ICT2000/yxiu/Data/CLOTH3D/dataset/stage_III


<h2>DataReader</h2>

This is the main class for I/O operations. Found at 'StarterKit/DataReader/read.py'.<br>
NOTE: competitors shall change the path to data if necessary (DataReader.SRC).

In [125]:
reader = DataReader()
reader.SRC = amass_track_1_dir

# Display utils used on this notebook require triangulated faces
def quads2tris(F):
    out = []
    for f in F:
        if len(f) == 3: out += [f]
        elif len(f) == 4: out += [[f[0],f[1],f[2]],
                                [f[0],f[2],f[3]]]
        else: print("This should not happen...")
    return np.array(out, np.int32)

# Display mesh
def display(V, F, C):
    if F.shape[1] != 3: F = quads2tris(F)
    fig = go.Figure(data=[
        go.Mesh3d(
            x=V[:,0],
            y=V[:,1],
            z=V[:,2],
            # i, j and k give the vertices of triangles
            i = F[:,0],
            j = F[:,1],
            k = F[:,2],
            vertexcolor = C,
            showscale=True
        )
    ])
    fig.show()

<h2>Metadata</h2>

First of all, we will show how to load the associated metadata of each sample and explain its structure and meaning.

In [126]:
import torch
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
import glob 

class AMASS_DS(Dataset):
    """AMASS: a pytorch loader for unified human motion capture dataset. http://amass.is.tue.mpg.de/"""

    def __init__(self, dataset_dir, num_betas=10):

        self.ds = {}
        for data_fname in glob.glob(os.path.join(dataset_dir, '*.pt')):
            k = os.path.basename(data_fname).replace('.pt','')
            self.ds[k] = torch.load(data_fname)
        self.num_betas = num_betas

    def __len__(self):
       return len(self.ds['trans'])

    def __getitem__(self, idx):
        data =  {k: self.ds[k][idx] for k in self.ds.keys()}

        # data['pose'] = data['pose'].reshape(24,3)
        # data['pose'][1,2] = 0.15
        # data['pose'][2,2] = -0.15
        # data['pose'] = data['pose'].flatten()

        data['root_orient'] = data['pose'][:3]
        data['pose_body'] = data['pose'][3:-6]
        data['pose_hand'] = data['pose'][-6:]
        data['betas'] = data['betas'][:self.num_betas]

        return data

num_betas = 10 # number of body parameters
testsplit_dir = os.path.join(work_dir, 'stage_III', 'train')

ds = AMASS_DS(dataset_dir=testsplit_dir, num_betas=num_betas)
print('Test split has %d datapoints.'%len(ds))

batch_size = 1
dataloader = DataLoader(ds, batch_size=batch_size, shuffle=True, num_workers=5)

Test split has 1424826 datapoints.


In [127]:
import trimesh
from human_body_prior.tools.omni_tools import colors
from human_body_prior.mesh import MeshViewer
from human_body_prior.mesh.sphere import points_to_spheres
from human_body_prior.tools.omni_tools import apply_mesh_tranfsormations_
from human_body_prior.tools.visualization_tools import imagearray2file
from notebook_tools import show_image

imw, imh=1600, 1600
mv = MeshViewer(width=imw, height=imh, use_offscreen=True)

In [128]:
from human_body_prior.body_model.body_model import BodyModel

bdata = next(iter(dataloader))
print(bdata['pose_body'].shape, bdata['trans'])

if bdata['gender'].item() == 0:
    bm_path = '../DataReader/smpl/model_f.pkl'
else:
    bm_path = '../DataReader/smpl/model_m.pkl'

bm = BodyModel(bm_path=bm_path, num_betas=num_betas, batch_size=batch_size)
faces = c2c(bm.f)

body = bm.forward(root_orient=bdata['root_orient'], pose_body=bdata['pose_body'], pose_hand=bdata['pose_hand'], betas=bdata['betas'], trans=bdata['trans'])

torch.Size([1, 63]) tensor([[-0.1518, -0.0030,  0.8632]])


In [129]:
orig_body_mesh = trimesh.Trimesh(vertices=c2c(body.v[0] - body.Jtr[0,0:1]), faces=c2c(body.f), vertex_colors=np.tile(colors['grey'], (6890, 1)))


In [130]:
display(orig_body_mesh.vertices, orig_body_mesh.faces, np.array([[0,255,0]]*orig_body_mesh.vertices.shape[0], np.uint8))

<h2>3D data</h2>

Human related 3D data is already covered by SMPL parameters provided along sequence metadata. Garment 3D data is stored as:
<ul>
    <li><b>.OBJ file:</b> widely used in the 3D industry. Mainly for storing mesh faces and UV map.</li>
    <li><b>.PC16 file:</b> animation data. A modification of the common PC2 format where floats are stored as 16-bits instead of 32-bits. Provides mesh vertex locations for each frame. NOTE: this format losses precision for large absolute values, for this reason, vertex location is relative to SMPL root joint.</li>
</ul>

<h3>How to read data?</h3>

DataReader contains high-level functions to avoid dealing with data files directly. For lower-level control, competitors can use I/O functions for these file formats, at 'StarterKit/DataReader/IO.py'.
<br>NOTE: DataReader will automatically apply 'trans' and 'zrot' to vertex locations, the competitors will require to apply them themselves when reading directly from data files.

In [131]:
printer = PrettyPrinter(indent=4)

data_dict = {}
for key in bdata.keys():
    data_dict[key] = c2c(bdata[key])
data_dict['vertices'] = np.array(orig_body_mesh.vertices)
data_dict['faces'] = np.array(orig_body_mesh.faces)

# printer.pprint(data_dict)

In [132]:
from prepare_data import outfit_types, fabric_types

frame = data_dict['frame'].item() # frame to visualize
sample = "%05d"%(data_dict['idx'].item())

print(f"sample:{sample}, frame:{frame}")

""" Human """
V = data_dict["vertices"]
F = data_dict["faces"]
# Vertex colors (for appealing visualization)
C = np.array([[255,255,255]]*V.shape[0], np.uint8)

trimesh.Trimesh(vertices=np.concatenate((V,C),1), faces=F).export("body.obj")

""" Garments """
outfit_onehot = data_dict['outfit'] != 0
garments_lst = list(np.nonzero(data_dict['outfit'][0])[0])
garments = [outfit_types[idx] for idx in garments_lst]
print(f"garments: {garments}")
for i,garment in enumerate(garments):
    _V = reader.read_garment_vertices(sample, garment, frame)
    _F = reader.read_garment_topology(sample, garment)
    _F = quads2tris(_F)
    trimesh.Trimesh(vertices=_V, faces=_F).export("cloth.obj")
    # Vertex colors
    _C = np.array([[255*i,0,255*(i-1)]]*_V.shape[0], np.uint8)
    # Merge human and garment meshes into one (for visualization purposes)
    F = np.concatenate((F,_F + V.shape[0]),0)
    V = np.concatenate((V,_V),0)  
    C = np.concatenate((C,_C),0)
    del _V
    del _F

""" DISPLAY """
display(V, F, C)

sample:03122, frame:229
garments: ['Jumpsuit']


<h2>Mesh color data</h2>

<h3>UV Mapping</h3>

During rendering, color is assigned to meshes through standard texture UV mapping. Explanation of the underlying mechanism of rendering a textured mesh is outside the scope of this notebook. We assume that competitors participating in Track 3 (texture recovering) have knowledge about this topic.<br>
NOTE: some graphic engines invert UV map vertical coordinate during the transformation to pixel space. Blender's graphic engines work like this. For an example on how UV to pixel mapping is performed, we refer to 'StaterKit/DataReader/util.py', function 'uv_to_pixel', at the end of the file.

<h3>Vertex Color</h3>

Alternatively, meshes can be colored by assigning a color to each vertex. This aproach depends directly on mesh topology and has limited capacity to display texture details. Nevertheless, we believe it is a valid approach and a good entry point for competitors that are not experts on the topic but still want to compete in Track 3.

We provide a functionality to gather the colors of each vertex of a given garment.<br>
NOTE: color is gathered at the EXACT vertex location, so it can be understood as a very coarse approximation of the actual mesh color. Additionally, 'plotly' module (for mesh visualization in this notebook) seems to have problems interpolating vertex colors for sudden changes in intensity (small details). Expect misbehaviours for some samples.

In [133]:
# Read garment vertices and faces again
garment = choice(garments)
V = reader.read_garment_vertices(sample, garment, frame)
F = reader.read_garment_topology(sample, garment)
# Read garment vertex colors
Vt, Ft = reader.read_garment_UVMap(sample, garment) # UV map required to estimate vertex color
C = reader.read_garment_vertex_colors(sample, garment, F, Vt, Ft)
if C.ndim == 1: C = np.stack([C]*V.shape[0], 0) # Plain RGB color
F = quads2tris(F)

""" DISPLAY """
display(V, F, C)